# Case - Data Preparation de um dataset para utilizá-lo na classificação de churn dos clientes

## Introdução

Uma empresa fictícia de telecomunicações dos Estados Unidos tem uma base de dados contendo diversas informações a respeito de seus clientes, desde a localização deles até com qual frequência utilizam a internet para assistir filmes. A partir disto, a empresa deseja que, após ser feita toda a limpeza e organização dados disponíveis, seja possível criar uma métrica de classificação chamada "churn", que indica o quanto a empresa perdeu de clientes. Ou seja, clientes classificados como churn são considerados "ex-clientes", não compram ou assinam mais os produtos da compania em questão.

## Objetivo do projeto

Projeto de data cleaning e data wrangling, com o objetivo de preparar uma base de dados que será utilizada para classificação de churn pela empresa.

## Settings

### Bibliotecas

Importando-se as bibliotecas necessárias para resolução deste caso.

In [5]:
import numpy as np
import pandas as pd
from ydata_profiling import ProfileReport       # lib para realizar análises automatizadas no dataset

# libs de visualização dos dados
import seaborn as sns
import matplotlib.pyplot as plt

# libs ScikitLearn para tratamento das features
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import scale, StandardScaler, OneHotEncoder, OrdinalEncoder

### Load dataset

Carregando-se o dataset da empresa,

In [6]:
customer = pd.read_excel('Telco_customer_churn.xlsx')

Exibindo o dataset,

In [7]:
display(customer)

CustomerID  Count        Country       State          City  Zip Code  \
0     3668-QPYBK      1  United States  California   Los Angeles     90003   
1     9237-HQITU      1  United States  California   Los Angeles     90005   
2     9305-CDSKC      1  United States  California   Los Angeles     90006   
3     7892-POOKP      1  United States  California   Los Angeles     90010   
4     0280-XJGEX      1  United States  California   Los Angeles     90015   
...          ...    ...            ...         ...           ...       ...   
7038  2569-WGERO      1  United States  California       Landers     92285   
7039  6840-RESVB      1  United States  California      Adelanto     92301   
7040  2234-XADUH      1  United States  California         Amboy     92304   
7041  4801-JZAZL      1  United States  California  Angelus Oaks     92305   
7042  3186-AJIEK      1  United States  California  Apple Valley     92308   

                    Lat Long   Latitude   Longitude  Gender  ...  \
0     33.964131, -118.272783  33.964131 -118.272783    Male  ...   
1      34.059281, -118.30742  34.059281 -118.307420  Female  ...   
2     34.048013, -118.293953  34.048013 -118.293953  Female  ...   
3     34.062125, -118.315709  34.062125 -118.315709  Female  ...   
4     34.039224, -118.266293  34.039224 -118.266293    Male  ...   
...                      ...        ...         ...     ...  ...   
7038  34.341737, -116.539416  34.341737 -116.539416  Female  ...   
7039  34.667815, -117.536183  34.667815 -117.536183    Male  ...   
7040  34.559882, -115.637164  34.559882 -115.637164  Female  ...   
7041     34.1678, -116.86433  34.167800 -116.864330  Female  ...   
7042  34.424926, -117.184503  34.424926 -117.184503    Male  ...   

            Contract Paperless Billing             Payment Method  \
0     Month-to-month               Yes               Mailed check   
1     Month-to-month               Yes           Electronic check   
2     Month-to-month               Yes           Electronic check   
3     Month-to-month               Yes           Electronic check   
4     Month-to-month               Yes  Bank transfer (automatic)   
...              ...               ...                        ...   
7038        Two year               Yes  Bank transfer (automatic)   
7039        One year               Yes               Mailed check   
7040        One year               Yes    Credit card (automatic)   
7041  Month-to-month               Yes           Electronic check   
7042        Two year               Yes  Bank transfer (automatic)   

      Monthly Charges Total Charges Churn Label Churn Value Churn Score  CLTV  \
0               53.85        108.15         Yes           1          86  3239   
1               70.70        151.65         Yes           1          67  2701   
2               99.65         820.5         Yes           1          86  5372   
3              104.80       3046.05         Yes           1          84  5003   
4              103.70        5036.3         Yes           1          89  5340   
...               ...           ...         ...         ...         ...   ...   
7038            21.15        1419.4          No           0          45  5306   
7039            84.80        1990.5          No           0          59  2140   
7040           103.20        7362.9          No           0          71  5560   
7041            29.60        346.45          No           0          59  2793   
7042           105.65        6844.5          No           0          38  5097   

                       Churn Reason  
0      Competitor made better offer  
1                             Moved  
2                             Moved  
3                             Moved  
4     Competitor had better devices  
...                             ...  
7038                            NaN  
7039                            NaN  
7040                            NaN  
7041                            NaN  
7042                            

In [14]:
customer.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7043 entries, 0 to 7042
Data columns (total 30 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   CustomerID         7043 non-null   object 
 1   City               7043 non-null   object 
 2   Zip Code           7043 non-null   int64  
 3   Lat Long           7043 non-null   object 
 4   Latitude           7043 non-null   float64
 5   Longitude          7043 non-null   float64
 6   Gender             7043 non-null   object 
 7   Senior Citizen     7043 non-null   object 
 8   Partner            7043 non-null   object 
 9   Dependents         7043 non-null   object 
 10  Tenure Months      7043 non-null   int64  
 11  Phone Service      7043 non-null   object 
 12  Multiple Lines     7043 non-null   object 
 13  Internet Service   7043 non-null   object 
 14  Online Security    7043 non-null   object 
 15  Online Backup      7043 non-null   object 
 16  Device Protection  7043 

## EDA

### Relatório automatizado

Utilizando a função ProfileReport, importada anteriormente, gera-se um relatório completo com análises descritivas e exploratórias de cada uma das colunas presentes no dataset. Isto é realizada conforme segue abaixo.

In [8]:
ProfileReport(customer)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

#### Dados ausentes e duplicados

Avaliando-se o relatório gerado acima, logo na primeira tabela de Overview tem-se as informações relacionadas a quantidade de linhas duplicadas, quantidade de dados nulos. Conforme ali descrito temos 2,2% de dados ausentes e nenhuma linha duplicada no dataset inteiro.
Verificando estes aspectos nas linhas de código abaixo.

In [10]:
# linhas duplicadas
customer.duplicated().sum()

0

Somando todas as linhas duplicadas do dataset tem-se um resultado de 0, o que condiz com a avaliação do relatório.

Analisando-se agora os dados ausentes,

In [12]:
# dados nulos
customer.isna().sum()

CustomerID              0
Count                   0
Country                 0
State                   0
City                    0
Zip Code                0
Lat Long                0
Latitude                0
Longitude               0
Gender                  0
Senior Citizen          0
Partner                 0
Dependents              0
Tenure Months           0
Phone Service           0
Multiple Lines          0
Internet Service        0
Online Security         0
Online Backup           0
Device Protection       0
Tech Support            0
Streaming TV            0
Streaming Movies        0
Contract                0
Paperless Billing       0
Payment Method          0
Monthly Charges         0
Total Charges           0
Churn Label             0
Churn Value             0
Churn Score             0
CLTV                    0
Churn Reason         5174
dtype: int64

Observando o resultado acima, temos que a única coluna com dados ausentes é a "Churn Reason" com 5174 dados nulos. Isto também é possível ser verificado no final da página de Overview do relatório. Lá consta um gráfico de Missing_values, onde consta que a coluna "Churn Reason" tem apenas 1869 dados não nulos, ou seja, 7043-1869 = 5174 dados nulos.

#### Alerts

Importante observar ainda neste relatório, que temos descritos alguns problemas observados na distribuição dos dados na aba "Alerts", que está no início do relatório. 

##### Dados Constantes

Fazendo uma observação nos alertas descritos, temos as colunas "Count", "Country" e "State" com dados constantes, ou seja, o mesmo dado em todas as 7043 linhas de dataset. Este tipo de coluna prejudica muito as medições do modelo de machine learning, além de não agregar nenhuma informação relevante ao problema de negócio em questão. Portanto, é conveniente removê-las do dataset.

In [13]:
customer.drop(columns = ['Count', 'Country', 'State'], inplace = True)